### Individual Project - Statistical Machine Learning - Charles PAYET

## 1. Initiation

In [4]:
Sys.setenv(LANG = "en")

# Data processing library
library(data.table)       # Data manipulation
library(plyr)             # Data manipulation
library(stringr)          # String, text processing
library(vita)             # Quickly check variable importance
library(dataPreparation)  # Data preparation library
library(woeBinning)       # Decision tree–based binning for numerical and categorical variables
library(Boruta)           # Variable selection

# Machine learning library
library(mlr)          # Machine learning framework
library(caret)         # Data processing and machine learning framework
library(MASS)          # LDA
library(randomForest)  # RF
library(gbm)           # Boosting Tree
library(xgboost)       # XGboost

In [5]:
#install.packages('funModeling')

## 2. Data summary and processing

### 2.1. Data summary

#### Read and print out some data

In [6]:
# Read train (full), test (holdout)
train_full <- read.csv('./data/Kaggle/input/bank_mkt_train.csv')  # Training dataset
test_holdout <- read.csv('./data/Kaggle/input/bank_mkt_test.csv')  # Holdout data set without response

In [7]:
# Print out to check the data type
str(train_full)

'data.frame':	7000 obs. of  21 variables:
 $ client_id     : int  2 3 4 5 6 7 8 9 14 15 ...
 $ age           : int  29 39 49 32 29 51 34 52 52 29 ...
 $ job           : Factor w/ 12 levels "admin.","blue-collar",..: 4 11 2 7 1 7 2 8 1 1 ...
 $ marital       : Factor w/ 4 levels "divorced","married",..: 3 2 2 3 3 2 2 2 2 3 ...
 $ education     : Factor w/ 8 levels "basic.4y","basic.6y",..: 4 3 2 7 4 7 1 4 7 7 ...
 $ default       : Factor w/ 2 levels "no","unknown": 1 2 2 1 2 2 1 1 1 1 ...
 $ housing       : Factor w/ 3 levels "no","unknown",..: 1 3 1 3 3 3 3 3 3 3 ...
 $ loan          : Factor w/ 3 levels "no","unknown",..: 1 1 1 1 1 1 1 1 1 1 ...
 $ contact       : Factor w/ 2 levels "cellular","telephone": 2 2 1 1 1 2 1 1 1 1 ...
 $ month         : Factor w/ 10 levels "apr","aug","dec",..: 7 5 8 7 4 5 8 8 8 5 ...
 $ day_of_week   : Factor w/ 5 levels "fri","mon","thu",..: 2 1 4 2 1 4 4 4 3 2 ...
 $ campaign      : int  3 6 2 3 2 1 1 1 3 1 ...
 $ pdays         : int  999 999 999 999 9

#### Correct the variable: campaign

Since campaign includes also the last contact, its value should be reduce by 1.

In [8]:
# Fix the value
train_full[, 'campaign'] <- train_full[, 'campaign'] - 1
test_holdout[, 'campaign'] <- test_holdout[, 'campaign'] - 1

# Quick check
min(train_full[, 'campaign'])  # Previously = 1
min(test_holdout[, 'campaign'])  # Previously = 1

[1] 0

[1] 0

#### Check and fix data error (if any)

In [9]:
# Check missing value
apply(is.na(train_full), 2, sum)

client_id            age            job        marital      education 
             0              0              0              0              0 
       default        housing           loan        contact          month 
             0              0              0              0              0 
   day_of_week       campaign          pdays       previous       poutcome 
             0              0              0              0              0 
  emp.var.rate cons.price.idx  cons.conf.idx      euribor3m    nr.employed 
             0              0              0              0              0 
     subscribe 
             0

#### Split train (full) data into train, valid, test (60:20:20)

In [10]:
set.seed(1)

train_idx <- caret::createDataPartition(y=train_full[, 'subscribe'], p=.6, list=F)
train <- train_full[train_idx, ]  # Train 60%
valid_test <- train_full[-train_idx, ]  # Valid + Test 40%

valid_idx <- caret::createDataPartition(y=valid_test[, 'subscribe'], p=.5, list=F)
valid <- valid_test[valid_idx, ]  # Valid 20%
test <- valid_test[-valid_idx, ]  # Test 20%

#### Check the target variable class distribution

In [11]:
# By number
table(train$subscribe)
table(valid$subscribe)
table(test$subscribe)


   0    1 
3721  479 


   0    1 
1247  153 


   0    1 
1210  190 

In [12]:
# By percentage
table(train$subscribe) / nrow(train)
table(valid$subscribe) / nrow(valid)
table(test$subscribe) / nrow(test)


        0         1 
0.8859524 0.1140476 


        0         1 
0.8907143 0.1092857 


        0         1 
0.8642857 0.1357143 

#### Simply check which variables are potentially important

Note: Running this permutation algorithm may take some time.

In [13]:
# PIMP-Algorithm For The Permutation Variable Importance Measure
# https://cran.r-project.org/web/packages/vita/vita.pdf
X <- train[, 2:(ncol(train)-1)]
y <- as.factor(train[, 'subscribe'])
rf_model <- randomForest(X, y, mtry=3, ntree=100, importance=T, seed=1)
pimp_varImp <- PIMP(X, y, rf_model, S=10, parallel=F, seed=123)

In [14]:
# Print out top most important variables
pimp_varImp$VarImp[order(pimp_varImp$VarImp[, 1], decreasing=T), ]

month      euribor3m   emp.var.rate    nr.employed cons.price.idx 
  4.390190e-02   3.533603e-02   2.769730e-02   2.691444e-02   2.533161e-02 
 cons.conf.idx            job            age      education       poutcome 
  2.417736e-02   7.023914e-03   5.379773e-03   3.310956e-03   3.137317e-03 
   day_of_week        contact       previous        marital          pdays 
  1.769988e-03   1.645544e-03   1.620392e-03   1.248047e-03   9.994050e-04 
       default           loan        housing       campaign 
  4.873672e-04  -1.735964e-05  -2.765152e-04  -6.482756e-04

### 2.2. Feature engineering

Hints:
- Focus on the most important variables.
- Create some framework for searching the new variables.

#### Add variable: month_spring

In [15]:
# Add new variable to train and test (holdout)
# Train, valid, test
train[, 'month_spring'] <- as.logical(train$month %in% c('mar', 'apr', 'may'))
valid[, 'month_spring'] <- as.logical(valid$month %in% c('mar', 'apr', 'may'))
test[, 'month_spring'] <- as.logical(test$month %in% c('mar', 'apr', 'may'))
# Test (holdout)
test_holdout[, 'month_spring'] <- as.logical(test_holdout$month %in% c('mar', 'apr', 'may'))

#### Add variable: month_summer

In [16]:
# Add new variable to train and test (holdout)
# Train, valid, test
train[, 'month_summer'] <- as.logical(train$month %in% c('jun', 'jul', 'aug'))
valid[, 'month_summer'] <- as.logical(valid$month %in% c('jun', 'jul', 'aug'))
test[, 'month_summer'] <- as.logical(test$month %in% c('jun', 'jul', 'aug'))
# Test (holdout)
test_holdout[, 'month_summer'] <- as.logical(test_holdout$month %in% c('jun', 'jul', 'aug'))

#### Add variable: month_autumn

In [17]:
# Add new variable to train and test (holdout)
# Train, valid, test
train[, 'month_autumn'] <- as.logical(train$month %in% c('sep', 'oct', 'nov'))
valid[, 'month_autumn'] <- as.logical(valid$month %in% c('sep', 'oct', 'nov'))
test[, 'month_autumn'] <- as.logical(test$month %in% c('sep', 'oct', 'nov'))
# Test (holdout)
test_holdout[, 'month_autumn'] <- as.logical(test_holdout$month %in% c('sep', 'oct', 'nov'))

#### Add variable: month_winter

In [18]:
# Add new variable to train and test (holdout)
# Train, valid, test
train[, 'month_winter'] <- as.logical(train$month %in% c('dec', 'jan', 'feb'))
valid[, 'month_winter'] <- as.logical(valid$month %in% c('dec', 'jan', 'feb'))
test[, 'month_winter'] <- as.logical(test$month %in% c('dec', 'jan', 'feb'))
# Test (holdout)
test_holdout[, 'month_winter'] <- as.logical(test_holdout$month %in% c('dec', 'jan', 'feb'))

#### Add variable: age > mean(age)

In [19]:
# Add new variable to train and test (holdout)
# Train, valid, test
train[, 'age_ge_mean'] <- as.logical(train$age > mean(train$age))
valid[, 'age_ge_mean'] <- as.logical(valid$age > mean(valid$age))
test[, 'age_ge_mean'] <- as.logical(test$age > mean(test$age))
# Test (holdout)
test_holdout[, 'age_ge_mean'] <- as.logical(test_holdout$age > mean(train$age))

#### Add variable: pdays_999

In [20]:
# Add new variable to train and test (holdout)
# pdays == 999 is a special value
# Train, valid, test
train[, 'pdays_999'] <- as.logical(train$pdays == 999)
valid[, 'pdays_999'] <- as.logical(valid$pdays == 999)
test[, 'pdays_999'] <- as.logical(test$pdays == 999)
# Test (holdout)
test_holdout[, 'pdays_999'] <- as.logical(test_holdout$pdays == 999)

### 2.3. Processing data

#### 2.3.1. Value transformation

- Categorical variables: remapping
- Continuous variables: discretization

Reference:  

Coussement, K., Lessmann, S., & Verstraeten, G. (2017). A comparative analysis of data preparation algorithms for customer churn prediction: A case study in the telecommunication industry. Decision Support Systems, 95, 27-36.

#### Get the list of categorical, boolean and numerical variables

In [21]:
# Get the IV and DV list name
# Dependent variable (DV)
dv_list <- c('subscribe')
# Independent variable (IV)
iv_list <- setdiff(colnames(train), dv_list)  # Exclude the target variable
iv_list <- setdiff(iv_list, 'client_id')  # Exclude the client_id

In [22]:
# Pick out categorical, boolean and numerical variable
iv_cat_list <- c()  # List to store categorical variable
iv_bool_list <- c()  # List to store boolean variable
iv_num_list <- c()  # List to store numerical variable
for (v in iv_list) {
    if (class(train[, v]) == 'factor') {  # Factor == categorical variable
        iv_cat_list <- c(iv_cat_list, v)
    } else if (class(train[, v]) == 'logical') {  # Logical == boolean variable
        iv_bool_list <- c(iv_bool_list, v)
    } else {  # Non-factor + Non-logical == numerical variable
        iv_num_list <- c(iv_num_list, v)
    }
}

#### Grouping (or remapping) categorical variables - Decision tree–based remapping

Reference:  

Package ‘woeBinning’: https://cran.r-project.org/web/packages/woeBinning/woeBinning.pdf

Test the variable remmaping on a categorical variable.

In [23]:
# Grouping 12 categories in the variable job onto 3 groups using WOE
binning_cat <- woe.binning(train, 'subscribe', 'job')
binning_cat

[[1]]
[1] "job"

[[2]]
                                                               Group.2
2  management + technician + misc. level neg. + blue-collar + services
3  management + technician + misc. level neg. + blue-collar + services
4  management + technician + misc. level neg. + blue-collar + services
5  management + technician + misc. level neg. + blue-collar + services
6  management + technician + misc. level neg. + blue-collar + services
7  management + technician + misc. level neg. + blue-collar + services
8  management + technician + misc. level neg. + blue-collar + services
1                                                               admin.
9                                                     misc. level pos.
10                                                    misc. level pos.
11                                                    misc. level pos.
12                                                    misc. level pos.
         Group.1       woe iv.total.final   1    0 col.perc.a col.perc.b
2    blue-collar -26.98343      0.1237265 235 2391  0.4906054  0.6425692
3   entrepreneur -26.98343      0.1237265 235 2391  0.4906054  0.6425692
4      housemaid -26.98343      0.1237265 235 2391  0.4906054  0.6425692
5     management -26.98343      0.1237265 235 2391  0.4906054  0.6425692
6       services -26.98343      0.1237265 235 2391  0.4906054  0.6425692
7     technician -26.98343      0.1237265 235 2391  0.4906054  0.6425692
8        unknown -26.98343      0.1237265 235 2391  0.4906054  0.6425692
1         admin.  15.07074      0.1237265 135  902  0.2818372  0.2424080
9        retired  68.22718      0.1237265 109  428  0.2275574  0.1150228
10 self-employed  68.22718      0.1237265 109  428  0.2275574  0.1150228
11       student  68.22718      0.1237265 109  428  0.2275574  0.1150228
12    unemployed  68.22718      0.1237265 109  428  0.2275574  0.1150228
       iv.bins
2  0.041005042
3  0.041005042
4  0.041005042
5  0.041005042
6  0.041005042
7  0.041005042
8  0.041005042
1  0.005942273
9  0.076779164
10 0.076779164
11 0.076779164
12 0.076779164

[[3]]
iv.total.final 
     0.1237265

In [24]:
# Apply the binning to data
tmp <- woe.binning.deploy(train, binning_cat, add.woe.or.dum.var='woe')
head(tmp[, c('job', 'job.binned', 'woe.job.binned')])

job          
1  housemaid    
4  self-employed
7  blue-collar  
14 technician   
15 management   
16 admin.       
   job.binned                                                         
1  management + technician + misc. level neg. + blue-collar + services
4  misc. level pos.                                                   
7  management + technician + misc. level neg. + blue-collar + services
14 management + technician + misc. level neg. + blue-collar + services
15 management + technician + misc. level neg. + blue-collar + services
16 admin.                                                             
   woe.job.binned
1  -26.98343     
4   68.22718     
7  -26.98343     
14 -26.98343     
15 -26.98343     
16  15.07074

Apply the variable remmaping for all categorical variables.

In [25]:
# Loop through all categorical variables
for (v in iv_cat_list) {
    
    # Remapping categorical variable on train data
    binning_cat <- woe.binning(train, 'subscribe', v)
    
    # Apply the binning to the train, valid and test data
    train <- woe.binning.deploy(train, binning_cat, add.woe.or.dum.var='woe')
    valid <- woe.binning.deploy(valid, binning_cat, add.woe.or.dum.var='woe')
    test <- woe.binning.deploy(test, binning_cat, add.woe.or.dum.var='woe')
    
    # Apply the binning to the test (holdout) data
    test_holdout <- woe.binning.deploy(test_holdout, binning_cat, add.woe.or.dum.var='woe')
}

#### Grouping (or discretizing) numerical variables - Decision tree–based discretization

Test the variable discretizing on a numerical variable.

In [26]:
# Grouping the variable age onto 4 groups using WOE
binning_num <- woe.binning(train, 'subscribe', 'age')
binning_num

[[1]]
[1] "age"

[[2]]
                 woe cutpoints.final cutpoints.final[-1] iv.total.final   1
(-Inf,26]  62.641510            -Inf                  26      0.1257925  46
(26,38]     1.589851              26                  38      0.1257925 223
(38,50]   -53.033993              38                  50      0.1257925  89
(50, Inf]  36.886531              50                 Inf      0.1257925 121
Missing           NA             Inf             Missing      0.1257925   0
             0 col.perc.a col.perc.b     iv.bins
(-Inf,26]  191  0.0960334 0.05133029 0.028002706
(26,38]   1705  0.4655532 0.45821016 0.000116744
(38,50]   1175  0.1858038 0.31577533 0.068929114
(50, Inf]  650  0.2526096 0.17468422 0.028743969
Missing      0  0.0000000 0.00000000          NA

[[3]]
iv.total.final 
     0.1257925

In [27]:
# Apply the binning to data
tmp <- woe.binning.deploy(train, binning_num, add.woe.or.dum.var='woe')
head(tmp[, c('age', 'age.binned', 'woe.age.binned')])

age age.binned woe.age.binned
1  29  (26,38]      1.589851    
4  32  (26,38]      1.589851    
7  34  (26,38]      1.589851    
14 39  (38,50]    -53.033993    
15 39  (38,50]    -53.033993    
16 33  (26,38]      1.589851

Apply the variable discretizing for all numerical variables.

In [28]:
# Loop through all numerical variables
for (v in iv_num_list) {
    
    # Discretizing numerical variable on train data
    binning_num <- woe.binning(train, 'subscribe', v)
    
    # Apply the binning to the train, valid and test data
    train <- woe.binning.deploy(train, binning_num, add.woe.or.dum.var='woe')
    valid <- woe.binning.deploy(valid, binning_num, add.woe.or.dum.var='woe')
    test <- woe.binning.deploy(test, binning_num, add.woe.or.dum.var='woe')
    
    # Apply the binning to the test (holdout) data
    test_holdout <- woe.binning.deploy(test_holdout, binning_num, add.woe.or.dum.var='woe')
}

#### Grouping (or discretizing) numerical variables - Equal frequency discretization

Reference:  

Tutorial to prepare train and test set using dataPreparation: https://cran.r-project.org/web/packages/dataPreparation/vignettes/train_test_prep.html

Test the variable discretizing on a numerical variable.

In [29]:
# Build the discretization
bins <- build_bins(dataSet=train, cols="age", n_bins=5, type="equal_freq", verbose=F)

# Print out to check
bins

$age
[1] -Inf   31   35   41   50  Inf

In [30]:
# Apply to the data
tmp <- fastDiscretization(dataSet=train, bins=bins, verbose=F)
setDF(tmp); setDF(train)  # Convert data.table to data.frame
head(tmp[, 'age'])

[1] ]-Inf, 31[ [31, 35[   [31, 35[   [35, 41[   [35, 41[   [31, 35[  
Levels: [31, 35[ [35, 41[ [41, 50[ [50, +Inf[ ]-Inf, 31[

Apply the variable discretizing for all numerical variables.

In [31]:
# Loop through all numerical variables
for (v in iv_num_list) {
    
    # Discretizing numerical variable on train data, n_bins=5
    bins <- build_bins(dataSet=train, cols=v, n_bins=5, type="equal_freq", verbose=F)
    
    # Apply the binning to the train, valid and test data
    tmp <- fastDiscretization(dataSet=train, bins=bins, verbose=F)
    setDF(tmp); setDF(train)  # Convert data.table to data.frame
    train[, paste0(v, '_freq_bin')] <- tmp[, v]  # Add new variable
    
    tmp <- fastDiscretization(dataSet=valid, bins=bins, verbose=F)
    setDF(tmp); setDF(valid)  # Convert data.table to data.frame
    valid[, paste0(v, '_freq_bin')] <- tmp[, v]  # Add new variable
    
    tmp <- fastDiscretization(dataSet=test, bins=bins, verbose=F)
    setDF(tmp); setDF(test)  # Convert data.table to data.frame
    test[, paste0(v, '_freq_bin')] <- tmp[, v]  # Add new variable
    
    # Apply the binning to the test (holdout) data
    tmp <- fastDiscretization(dataSet=test_holdout, bins=bins, verbose=F)
    setDF(tmp); setDF(test_holdout)  # Convert data.table to data.frame
    test_holdout[, paste0(v, '_freq_bin')] <- tmp[, v]  # Add new variable
}

#### Grouping (or discretizing) numerical variables - Equal width discretization

Test the variable discretizing on a numerical variable.

In [32]:
# Build the discretization
bins <- build_bins(dataSet=train, cols="age", n_bins=5, type="equal_width", verbose=F)

# Print out to check
bins

$age
[1] 19.0 32.8 46.6 60.4 74.2 88.0

In [33]:
# Apply to the data
tmp <- fastDiscretization(dataSet=train, bins=bins, verbose=F)
setDF(tmp); setDF(train)  # Convert data.table to data.frame
head(tmp[, 'age'])

[1] [19, 32.8[   [19, 32.8[   [32.8, 46.6[ [32.8, 46.6[ [32.8, 46.6[
[6] [32.8, 46.6[
Levels: [19, 32.8[ [32.8, 46.6[ [46.6, 60.4[ [60.4, 74.2[ [74.2, 88]

Apply the variable discretizing for all numerical variables.

In [34]:
# Loop through all numerical variables
for (v in iv_num_list) {
    
    # Discretizing numerical variable on train data, n_bins=5
    bins <- build_bins(dataSet=train, cols=v, n_bins=5, type="equal_width", verbose=F)
    
    # Apply the binning to the train, valid and test data
    tmp <- fastDiscretization(dataSet=train, bins=bins, verbose=F)
    setDF(tmp); setDF(train)  # Convert data.table to data.frame
    train[, paste0(v, '_width_bin')] <- tmp[, v]  # Add new variable
    
    tmp <- fastDiscretization(dataSet=valid, bins=bins, verbose=F)
    setDF(tmp); setDF(valid)  # Convert data.table to data.frame
    valid[, paste0(v, '_width_bin')] <- tmp[, v]  # Add new variable
    
    tmp <- fastDiscretization(dataSet=test, bins=bins, verbose=F)
    setDF(tmp); setDF(test)  # Convert data.table to data.frame
    test[, paste0(v, '_width_bin')] <- tmp[, v]  # Add new variable
    
    # Apply the binning to the test (holdout) data
    tmp <- fastDiscretization(dataSet=test_holdout, bins=bins, verbose=F)
    setDF(tmp); setDF(test_holdout)  # Convert data.table to data.frame
    test_holdout[, paste0(v, '_width_bin')] <- tmp[, v]  # Add new variable
}

#### 2.3.2. Value representation

- Dummy coding
- Incidence replacement
- Weight of evidence (WoE conversion)

Reference:  

Coussement, K., Lessmann, S., & Verstraeten, G. (2017). A comparative analysis of data preparation algorithms for customer churn prediction: A case study in the telecommunication industry. Decision Support Systems, 95, 27-36.

All about Categorical Variable Encoding: https://towardsdatascience.com/all-about-categorical-variable-encoding-305f3361fd02

#### Get the updated list of categorical, boolean and numerical variables

In [35]:
# Get the IV and DV list name
# Dependent variable (DV)
dv_list <- c('subscribe')
# Independent variable (IV)
iv_list <- setdiff(colnames(train), dv_list)  # Exclude the target variable
iv_list <- setdiff(iv_list, 'client_id')  # Exclude the client_id

In [36]:
# Pick out categorical, boolean and numerical variable
iv_cat_list <- c()  # List to store categorical variable
iv_bool_list <- c()  # List to store boolean variable
iv_num_list <- c()  # List to store numerical variable
for (v in iv_list) {
    if (class(train[, v]) == 'factor') {  # Factor == categorical variable
        iv_cat_list <- c(iv_cat_list, v)
    } else if (class(train[, v]) == 'logical') {  # Logical == boolean variable
        iv_bool_list <- c(iv_bool_list, v)
    } else {  # Non-factor + Non-logical == numerical variable
        iv_num_list <- c(iv_num_list, v)
    }
}

#### Convert categorical variables to dummy

Test the variable representation on a categorical variable.

In [37]:
# Build the dummy encoding
encoding <- build_encoding(dataSet=train, cols="job", verbose=F)

In [38]:
# Transform the categorical variable
tmp <- one_hot_encoder(dataSet=train, encoding=encoding, type='logical', drop=F, verbose=F)
setDF(tmp)
tmp <- tmp[, -ncol(tmp)]
head(tmp[, 84:ncol(tmp)])

job.admin. job.blue.collar job.entrepreneur job.housemaid job.management
1 FALSE      FALSE           FALSE             TRUE         FALSE         
2 FALSE      FALSE           FALSE            FALSE         FALSE         
3 FALSE       TRUE           FALSE            FALSE         FALSE         
4 FALSE      FALSE           FALSE            FALSE         FALSE         
5 FALSE      FALSE           FALSE            FALSE          TRUE         
6  TRUE      FALSE           FALSE            FALSE         FALSE         
  job.retired job.self.employed job.services job.student job.technician
1 FALSE       FALSE             FALSE        FALSE       FALSE         
2 FALSE        TRUE             FALSE        FALSE       FALSE         
3 FALSE       FALSE             FALSE        FALSE       FALSE         
4 FALSE       FALSE             FALSE        FALSE        TRUE         
5 FALSE       FALSE             FALSE        FALSE       FALSE         
6 FALSE       FALSE             FALSE        FALSE       FALSE         
  job.unemployed
1 FALSE         
2 FALSE         
3 FALSE         
4 FALSE         
5 FALSE         
6 FALSE

Apply the variable representation for all categorical variables.

In [39]:
# Loop through all categorical variables
for (v in iv_cat_list) {
    
    # Representing categorical variable on train data
    encoding <- build_encoding(dataSet=train, cols=v, verbose=F)
    
    # Apply the binning to the train, valid and test data
    train <- one_hot_encoder(dataSet=train, encoding=encoding, type='logical', drop=F, verbose=F)
    setDF(train)
    train <- train[, -ncol(train)]  # Drop the last dummy column
    
    valid <- one_hot_encoder(dataSet=valid, encoding=encoding, type='logical', drop=F, verbose=F)
    setDF(valid)
    valid <- valid[, -ncol(valid)]  # Drop the last dummy column
    
    test <- one_hot_encoder(dataSet=test, encoding=encoding, type='logical', drop=F, verbose=F)
    setDF(test)
    test <- test[, -ncol(test)]  # Drop the last dummy column
    
    # Apply the binning to the test (holdout) data
    test_holdout <- one_hot_encoder(dataSet=test_holdout, encoding=encoding, type='logical', drop=F, verbose=F)
    setDF(test_holdout)
    test_holdout <- test_holdout[, -ncol(test_holdout)]  # Drop the last dummy column
}

#### Represent categorical variables using incidence of target variable

Test the variable representation on a categorical variable.

In [40]:
# Find the incidence rates per category of a variable
tb <- table(train$job, train$subscribe)
incidence_map <- data.frame('v1'=rownames(tb), 'v2'=tb[, '1'] / (tb[, '0'] + tb[, '1']))
colnames(incidence_map) <- c('job', 'job_incidence')
incidence_map

job           job_incidence
admin.        admin.        0.13018322   
blue-collar   blue-collar   0.08278146   
entrepreneur  entrepreneur  0.10493827   
housemaid     housemaid     0.08256881   
management    management    0.11006289   
retired       retired       0.24102564   
self-employed self-employed 0.13548387   
services      services      0.07616708   
student       student       0.29347826   
technician    technician    0.09571429   
unemployed    unemployed    0.14736842   
unknown       unknown       0.04166667

In [41]:
# Convert the categories with incidences
tmp <- plyr::join(x=train, y=incidence_map, by='job', type="left", match="all")  # Left join
head(tmp[, c('job', 'job_incidence')])

job           job_incidence
1 housemaid     0.08256881   
2 self-employed 0.13548387   
3 blue-collar   0.08278146   
4 technician    0.09571429   
5 management    0.11006289   
6 admin.        0.13018322

Apply the variable representation for all categorical variables.

In [42]:
# Loop through all categorical variables
for (v in iv_cat_list) {
    
    # Find the incidence rates per category of a variable
    tb <- table(train[, v], train[, 'subscribe'])
    incidence_map <- data.frame('v1'=rownames(tb), 'v2'=tb[, '1'] / (tb[, '0'] + tb[, '1']))
    colnames(incidence_map) <- c(v, paste0(v, '_incidence'))  # Rename the columns to join
    
    # Apply the variable representation to the train, valid and test data
    train <- plyr::join(x=train, y=incidence_map, by=v, type="left", match="all")
    valid <- plyr::join(x=valid, y=incidence_map, by=v, type="left", match="all")
    test <- plyr::join(x=test, y=incidence_map, by=v, type="left", match="all")
    
    # Apply the binning to the test (holdout) data
    test_holdout <- plyr::join(x=test_holdout, y=incidence_map, by=v, type="left", match="all")
}

#### Represent categorical variables using weight-of-evidence conversion

Test the variable representation on a categorical variable.

In [43]:
# Find the WOE per category of a variable
tb <- table(train$job, train$subscribe)
woe_map <- data.frame('v1'=rownames(tb), 'v2'=log(tb[, '1'] / tb[, '0']))
colnames(woe_map) <- c('job', 'job_woe')
woe_map

job           job_woe   
admin.        admin.        -1.8993397
blue-collar   blue-collar   -2.4051417
entrepreneur  entrepreneur  -2.1435204
housemaid     housemaid     -2.4079456
management    management    -2.0900988
retired       retired       -1.1470647
self-employed self-employed -1.8533174
services      services      -2.4956019
student       student       -0.8785504
technician    technician    -2.2457778
unemployed    unemployed    -1.7553918
unknown       unknown       -3.1354942

In [44]:
# Convert the categories with WOE
tmp <- plyr::join(x=train, y=woe_map, by='job', type="left", match="all")  # Left join
head(tmp[, c('job', 'job_woe')])

job           job_woe  
1 housemaid     -2.407946
2 self-employed -1.853317
3 blue-collar   -2.405142
4 technician    -2.245778
5 management    -2.090099
6 admin.        -1.899340

Apply the variable representation for all categorical variables.

In [45]:
# Loop through all categorical variables
for (v in iv_cat_list) {
    
    # Find the incidence rates per category of a variable
    tb <- table(train[, v], train[, 'subscribe'])
    woe_map <- data.frame('v1'=rownames(tb), 'v2'=log(tb[, '1'] / tb[, '0']))
    colnames(woe_map) <- c(v, paste0(v, '_woe'))  # Rename the columns to join
    
    # Apply the variable representation to the train, valid and test data
    train <- plyr::join(x=train, y=woe_map, by=v, type="left", match="all")
    valid <- plyr::join(x=valid, y=woe_map, by=v, type="left", match="all")
    test <- plyr::join(x=test, y=woe_map, by=v, type="left", match="all")
    
    # Apply the binning to the test (holdout) data
    test_holdout <- plyr::join(x=test_holdout, y=woe_map, by=v, type="left", match="all")
}

#### 2.3.3. Others variable transformations

#### Log transformation numerical variable

In [46]:
# Transform the variable age on train and test (holdout)
# Train, valid, test
train[, 'age_log'] <- log(train[, 'age'])
valid[, 'age_log'] <- log(valid[, 'age'])
test[, 'age_log'] <- log(test[, 'age'])
# Test (holdout)
test_holdout[, 'age_log'] <- log(test_holdout[, 'age'])

#### Standardize numerical variable

In [47]:
# Standardize the variable age on train and test (holdout)
# Train, valid, test
train[, 'age_scaled'] <- scale(train[, 'age'], center=T, scale=T)  # sd = 1, mean = 0
valid[, 'age_scaled'] <- scale(valid[, 'age'], center=T, scale=T)  # sd = 1, mean = 0
test[, 'age_scaled'] <- scale(test[, 'age'], center=T, scale=T)  # sd = 1, mean = 0
# Test (holdout)
test_holdout[, 'age_scaled'] <- scale(test_holdout[, 'age'], center=T, scale=T)  # sd = 1, mean = 0

### 2.4. Variable selection

Reference:  

Verbeke, W., Dejaeger, K., Martens, D., Hur, J., & Baesens, B. (2012). New insights into churn prediction in the telecommunication sector: A profit driven data mining approach. European Journal of Operational Research, 218(1), 211-229.

Boruta: https://www.datacamp.com/community/tutorials/feature-selection-R-boruta

#### Get the updated list of categorical, boolean and numerical variables

In [48]:
# Get the IV and DV list name
# Dependent variable (DV)
dv_list <- c('subscribe')
# Independent variable (IV)
iv_list <- setdiff(colnames(train), dv_list)  # Exclude the target variable
iv_list <- setdiff(iv_list, 'client_id')  # Exclude the client_id

In [49]:
# Pick out categorical, boolean and numerical variable
iv_cat_list <- c()  # List to store categorical variable
iv_bool_list <- c()  # List to store boolean variable
iv_num_list <- c()  # List to store numerical variable
for (v in iv_list) {
    if (class(train[, v]) == 'factor') {  # Factor == categorical variable
        iv_cat_list <- c(iv_cat_list, v)
    } else if (class(train[, v]) == 'logical') {  # Logical == boolean variable
        iv_bool_list <- c(iv_bool_list, v)
    } else {  # Non-factor + Non-logical == numerical variable
        iv_num_list <- c(iv_num_list, v)
    }
}

#### 2.4.1. Variable correcting and filtering

#### Check and correct +/-Inf values (if any)

In [50]:
# Check missing value
# Train, valid, test
sum(apply(sapply(train, is.infinite), 2, sum))
sum(apply(sapply(valid, is.infinite), 2, sum))
sum(apply(sapply(test, is.infinite), 2, sum))
# Test (holdout)
sum(apply(sapply(test_holdout, is.infinite), 2, sum))

[1] 20

[1] 3

[1] 2

[1] 18

In [51]:
# Impute +/-Inf value by NA
# Train, valid, test
train[sapply(train, is.infinite)] <- NA
valid[sapply(valid, is.infinite)] <- NA
test[sapply(test, is.infinite)] <- NA
# Test (holdout)
test_holdout[sapply(test_holdout, is.infinite)] <- NA

#### Check and correct missing values (if any)

In [52]:
# Check missing value
# Train, valid, test
sum(apply(is.na(train), 2, sum))
sum(apply(is.na(valid), 2, sum))
sum(apply(is.na(test), 2, sum))
# Test (holdout)
sum(apply(is.na(test_holdout), 2, sum))

[1] 20

[1] 3

[1] 2

[1] 20

In [53]:
# Impute missing value in numerical variable by mean
for (v in iv_num_list) {
    # Train, valid, test
    train[is.na(train[, v]), v] <- mean(train[, v], na.rm=T)
    valid[is.na(valid[, v]), v] <- mean(valid[, v], na.rm=T)
    test[is.na(test[, v]), v] <- mean(test[, v], na.rm=T)
    
    # Test (holdout)
    test_holdout[is.na(test_holdout[, v]), v] <- mean(test_holdout[, v], na.rm=T)
}

#### Drop categorical variables (all were processed)

In [54]:
for (v in iv_cat_list) {
    # Train, valid, test
    train[, v] <- NULL
    valid[, v] <- NULL
    test[, v] <- NULL
    
    # Test (holdout)
    test_holdout[, v] <- NULL
}

#### Convert boolean variable to numerical

In [55]:
# Convert boolean to int
for (v in iv_bool_list) {
    # Train, valid, test
    train[, v] <- as.integer(train[, v])
    valid[, v] <- as.integer(valid[, v])
    test[, v] <- as.integer(test[, v])
    
    # Test (holdout)
    test_holdout[, v] <- as.integer(test_holdout[, v])
}

#### Drop constant variable (i.e. variance=0)

In [56]:
# Find the constant variable
var_list <- c()
for (v in c(iv_num_list, iv_bool_list)) {
    var_list <- c(var_list, var(train[, v], na.rm=T))
}
constant_var <- c(iv_num_list, iv_bool_list)[var_list == 0]
constant_var

[1] "woe.pdays.binned"            "pdays.binned_incidence"     
[3] "previous_freq_bin_incidence" "pdays.binned_woe"           
[5] "previous_freq_bin_woe"       "pdays.binned...Inf.999."    
[7] "pdays.binned..999. Inf."

In [57]:
# Drop the constant variable
for (v in constant_var) {
    # Train, valid, test
    train[, v] <- NULL
    valid[, v] <- NULL
    test[, v] <- NULL
    
    # Test (holdout)
    test_holdout[, v] <- NULL
}

#### 2.4.2. Variable selection: Fisher Score

In [58]:
FisherScore <- function(basetable, depvar, IV_list) {
  "
  This function calculate the Fisher score of a variable.
  
  Ref:
  ---
  Verbeke, W., Dejaeger, K., Martens, D., Hur, J., & Baesens, B. (2012). New insights into churn prediction in the telecommunication sector: A profit driven data mining approach. European Journal of Operational Research, 218(1), 211-229.
  "
  
  # Get the unique values of dependent variable
  DV <- unique(basetable[, depvar])
  
  IV_FisherScore <- c()
  
  for (v in IV_list) {
    fs <- abs((mean(basetable[which(basetable[, depvar]==DV[1]), v]) - mean(basetable[which(basetable[, depvar]==DV[2]), v]))) /
      sqrt((var(basetable[which(basetable[, depvar]==DV[1]), v]) + var(basetable[which(basetable[, depvar]==DV[2]), v])))
    IV_FisherScore <- c(IV_FisherScore, fs)
  }
  
  return(data.frame(IV=IV_list, fisher_score=IV_FisherScore))
}

varSelectionFisher <- function(basetable, depvar, IV_list, num_select=20) {
  "
  This function will calculate the Fisher score for all IVs and select the best
  top IVs.

  Assumption: all variables of input dataset are converted into numeric type.
  "
  
  fs <- FisherScore(basetable, depvar, IV_list)  # Calculate Fisher Score for all IVs
  num_select <- min(num_select, ncol(basetable))  # Top N IVs to be selected
  return(as.vector(fs[order(fs$fisher_score, decreasing=T), ][1:num_select, 'IV']))
}

In [59]:
# Calculate Fisher Score for all variable
# Get the IV and DV list
dv_list <- c('subscribe')  # DV list
iv_list <- setdiff(names(train), dv_list)  # IV list excluded DV
iv_list <- setdiff(iv_list, 'client_id')  # Excluded the client_id
fs <- FisherScore(train, dv_list, iv_list)
head(fs)

IV             fisher_score
1 age            0.0364485   
2 campaign       0.1443533   
3 pdays          0.4343708   
4 previous       0.3454339   
5 emp.var.rate   0.6531280   
6 cons.price.idx 0.3030515

In [60]:
# Select top 20 variables according to the Fisher Score
best_fs_var <- varSelectionFisher(train, dv_list, iv_list, num_select=50)
head(best_fs_var, 10)

[1] "nr.employed_freq_bin_woe"         "woe.nr.employed.binned"          
 [3] "nr.employed.binned_woe"           "nr.employed_freq_bin_incidence"  
 [5] "nr.employed.binned_incidence"     "nr.employed_width_bin_woe"       
 [7] "nr.employed"                      "emp.var.rate_width_bin_woe"      
 [9] "euribor3m_freq_bin_woe"           "nr.employed.binned...Inf.5076.2."

In [61]:
# Apply variable selection to the data
# Train
var_select <- names(train)[names(train) %in% best_fs_var]
train_processed <- train[, c('client_id', var_select, 'subscribe')]
# Valid
var_select <- names(valid)[names(valid) %in% best_fs_var]
valid_processed <- valid[, c('client_id', var_select, 'subscribe')]
# Test
var_select <- names(test)[names(test) %in% best_fs_var]
test_processed <- test[, c('client_id', var_select, 'subscribe')]
# Test (holdout)
var_select <- names(test_holdout)[names(test_holdout) %in% best_fs_var]
test_holdout_processed <- test_holdout[, c('client_id', var_select)]

### 2.5. Finalize data processing

In [62]:
# Check if train and test (holdout) have same variables
# Train, valid, test
dim(train_processed)
dim(valid_processed)
dim(test_processed)
# Test (holdout)
dim(test_holdout_processed)

[1] 4200   52

[1] 1400   52

[1] 1400   52

[1] 3000   51

In [63]:
# Rename the data columns
for (v in colnames(train_processed)) {
    
    # Fix the column name
    fix_name <- str_replace_all(v, "[^[:alnum:] ]", "_")
    fix_name <- gsub(' +', '', fix_name) 
    
    # Train, valid, test
    colnames(train_processed)[colnames(train_processed) == v] <- fix_name
    colnames(valid_processed)[colnames(valid_processed) == v] <- fix_name
    colnames(test_processed)[colnames(test_processed) == v] <- fix_name
    
    # Test (holdout)
    colnames(test_holdout_processed)[colnames(test_holdout_processed) == v] <- fix_name
}

In [64]:
# Print out to check
head(train_processed)

client_id pdays emp_var_rate euribor3m nr_employed pdays_999 woe_month_binned
1  2        999    1.1         4.858     5191.0      1         -33.39693       
2  5        999   -1.8         1.299     5099.1      1         -33.39693       
3  8        999   -0.1         4.153     5195.8      1         -33.39693       
4 21        999    1.4         4.967     5228.1      1         -33.39693       
5 22        999    1.4         4.964     5228.1      1         -33.39693       
6 24        999    1.4         4.964     5228.1      1         -33.39693       
  woe_emp_var_rate_binned woe_cons_price_idx_binned woe_cons_conf_idx_binned
1 -94.56851               -123.93836                   9.414245             
2  44.14570                 30.17728                 -59.006784             
3  44.14570                -33.24684                 -59.006784             
4 -94.56851                -33.24684                -106.548634             
5 -94.56851                -33.24684                -106.548634             
6 -94.56851                -33.24684                -106.548634             
  ... euribor3m_binned_woe nr_employed_binned_woe emp_var_rate_freq_bin_woe
1 ... -2.616464            -2.896025              -3.289431                
2 ... -2.616464            -1.971674              -1.429056                
3 ... -2.616464            -2.896025              -2.363994                
4 ... -2.616464            -2.896025              -2.876386                
5 ... -2.616464            -2.896025              -2.876386                
6 ... -2.616464            -2.896025              -2.876386                
  euribor3m_freq_bin_woe nr_employed_freq_bin_woe emp_var_rate_width_bin_woe
1 -3.192275              -3.289431                -2.995732                 
2 -2.098587              -1.974348                -1.540039                 
3 -2.098587              -2.363994                -2.370244                 
4 -2.833213              -2.876386                -2.995732                 
5 -2.833213              -2.876386                -2.995732                 
6 -2.833213              -2.876386                -2.995732                 
  cons_conf_idx_width_bin_woe euribor3m_width_bin_woe nr_employed_width_bin_woe
1 -2.671493                   -2.929108               -2.896025                
2 -1.876394                   -1.171029               -1.691018                
3 -2.756119                   -2.639057               -2.896025                
4 -2.671493                   -2.929108               -2.896025                
5 -2.671493                   -2.929108               -2.896025                
6 -2.671493                   -2.929108               -2.896025                
  subscribe
1 0        
2 0        
3 0        
4 0        
5 1        
6 0

In [167]:
write.csv(train_processed, './data/Kaggle/output/train_processed.csv', row.names=FALSE)

## 3. Methodology

### 3.1. Logistic Regression model

In [65]:
# Set up cross-validation
rdesc = makeResampleDesc("CV", iters=5, predict="both")

# Define the model
learner <- makeLearner("classif.logreg", predict.type="prob", fix.factors.prediction=T)

# Define the task
train_task <- makeClassifTask(id="bank_train", data=train_processed[, -1], target="subscribe")

# Set hyper parameter tuning
tune_params <- makeParamSet(
)
ctrl = makeTuneControlGrid()

# Run the hyper parameter tuning with k-fold CV
if (length(tune_params$pars) > 0) {
    # Run parameter tuning
    res <- tuneParams(learner, task=train_task, resampling=rdesc,
      par.set=tune_params, control=ctrl, measures=list(mlr::auc))
    
    # Extract best model
    best_learner <- res$learner
    
} else {
    # Simple cross-validation
    res <- resample(learner, train_task, rdesc, measures=list(mlr::auc, setAggregation(mlr::auc, train.mean)))
    
    # No parameter for tuning, only 1 best learner
    best_learner <- learner
}

Resampling: cross-validation
Measures:             auc.train   auc.test    
Warning message in predict.lm(object, newdata, se.fit, scale = 1, type = if (type == :
"prediction from a rank-deficient fit may be misleading"Warning message in predict.lm(object, newdata, se.fit, scale = 1, type = if (type == :
"prediction from a rank-deficient fit may be misleading"[Resample] iter 1:    0.7942316   0.7487939   
Warning message in predict.lm(object, newdata, se.fit, scale = 1, type = if (type == :
"prediction from a rank-deficient fit may be misleading"Warning message in predict.lm(object, newdata, se.fit, scale = 1, type = if (type == :
"prediction from a rank-deficient fit may be misleading"[Resample] iter 2:    0.7873690   0.7697736   
Warning message in predict.lm(object, newdata, se.fit, scale = 1, type = if (type == :
"prediction from a rank-deficient fit may be misleading"Warning message in predict.lm(object, newdata, se.fit, scale = 1, type = if (type == :
"prediction from a rank-defi

In [66]:
# Retrain the model with tbe best hyper-parameters
best_md <- mlr::train(best_learner, train_task)

In [67]:
# Make prediction on valid data
pred <- predict(best_md, newdata=valid_processed[, -1])
performance(pred, measures=mlr::auc)

Warning message in predict.lm(object, newdata, se.fit, scale = 1, type = if (type == :
"prediction from a rank-deficient fit may be misleading"

auc 
0.8066025

In [68]:
# Make prediction on test data
pred <- predict(best_md, newdata=test_processed[, -1])
performance(pred, measures=mlr::auc)

Warning message in predict.lm(object, newdata, se.fit, scale = 1, type = if (type == :
"prediction from a rank-deficient fit may be misleading"

auc 
0.8129752

In [69]:
# Make prediction on test (holdout) data
pred <- predict(best_md, newdata=test_holdout_processed[, -1])
pred

Warning message in predict.lm(object, newdata, se.fit, scale = 1, type = if (type == :
"prediction from a rank-deficient fit may be misleading"

Prediction: 3000 observations
predict.type: prob
threshold: 0=0.50,1=0.50
time: 0.00
     prob.0     prob.1 response
1 0.9481784 0.05182160        0
2 0.9578501 0.04214988        0
3 0.5400638 0.45993620        0
4 0.9289286 0.07107139        0
5 0.9643685 0.03563154        0
6 0.9281973 0.07180266        0
... (#rows: 3000, #cols: 3)

In [70]:
# Output predicted file
output <- data.frame(client_id=test_holdout$client_id, subscribe=pred$data$prob.1)
write.csv(output, './data/Kaggle/output/lr_submission_6.csv', row.names=FALSE)

### 3.2. RandomForest model

In [168]:
# Set up cross-validation
rdesc = makeResampleDesc("CV", iters=10)

# Define the model
learner <- makeLearner("classif.randomForest", predict.type="prob", fix.factors.prediction=T)

# Define the task
train_task <- makeClassifTask(id="bank_train", data=train_processed[, -1], target="subscribe")

# Set hyper parameter tuning
tune_params <- makeParamSet(
  makeDiscreteParam('ntree', value=c(100, 250, 500, 750, 1000)),
  makeDiscreteParam('mtry', value=round(sqrt((ncol(train_processed)-1) * c(0.1, 0.25, 0.5, 1, 2, 4))))
)
ctrl = makeTuneControlGrid()

# Run the hyper parameter tuning with k-fold CV
if (length(tune_params$pars) > 0) {
    # Run parameter tuning
    res <- tuneParams(learner, task=train_task, resampling=rdesc,
      par.set=tune_params, control=ctrl, measures=list(mlr::auc))
    
    # Extract best model
    best_learner <- res$learner
    
} else {
    # Simple cross-validation
    res <- resample(learner, train_task, rdesc, measures=list(mlr::auc))
    
    # No parameter for tuning, only 1 best learner
    best_learner <- learner
}

[Tune] Started tuning learner classif.randomForest for parameter set:
          Type len Def               Constr Req Tunable Trafo
ntree discrete   -   - 100,250,500,750,1000   -    TRUE     -
mtry  discrete   -   -        2,4,5,7,10,14   -    TRUE     -
With control class: TuneControlGrid
Imputation value: -0
[Tune-x] 1: ntree=100; mtry=2
[Tune-y] 1: auc.test.mean=0.7215642; time: 0.1 min
[Tune-x] 2: ntree=250; mtry=2
[Tune-y] 2: auc.test.mean=0.7138911; time: 0.2 min
[Tune-x] 3: ntree=500; mtry=2
[Tune-y] 3: auc.test.mean=0.7278153; time: 0.4 min
[Tune-x] 4: ntree=750; mtry=2
[Tune-y] 4: auc.test.mean=0.7325165; time: 0.7 min
[Tune-x] 5: ntree=1000; mtry=2
[Tune-y] 5: auc.test.mean=0.7301312; time: 0.9 min
[Tune-x] 6: ntree=100; mtry=4
[Tune-y] 6: auc.test.mean=0.7188716; time: 0.1 min
[Tune-x] 7: ntree=250; mtry=4
[Tune-y] 7: auc.test.mean=0.7294043; time: 0.3 min
[Tune-x] 8: ntree=500; mtry=4
[Tune-y] 8: auc.test.mean=0.7301572; time: 0.5 min
[Tune-x] 9: ntree=750; mtry=4
[Tune-y]

In [169]:
# Retrain the model with tbe best hyper-parameters
best_md <- mlr::train(best_learner, train_task)

In [170]:
# Make prediction on valid data
pred <- predict(best_md, newdata=valid_processed[, -1])
performance(pred, measures=mlr::auc)

auc 
0.7613278

In [171]:
# Make prediction on test data
pred <- predict(best_md, newdata=test_processed[, -1])
performance(pred, measures=mlr::auc)

auc 
0.7273619

In [172]:
# Make prediction on test data
pred <- predict(best_md, newdata=test_holdout_processed[, -1])
pred

Prediction: 3000 observations
predict.type: prob
threshold: 0=0.50,1=0.50
time: 0.06
  prob.0 prob.1 response
1  1.000  0.000        0
2  1.000  0.000        0
3  0.726  0.274        0
4  1.000  0.000        0
5  1.000  0.000        0
6  1.000  0.000        0
... (#rows: 3000, #cols: 3)

In [307]:
# Output predicted file
output <- data.frame(client_id=test_holdout$client_id, subscribe=pred$data$prob.1)
write.csv(output, './data/Kaggle/output/rf_submission_5.csv', row.names=FALSE)

### 3.3 Decision Tree

In [308]:
#create a task
trainTask <- makeClassifTask(data = train_processed,target = "subscribe")
testTask <- makeClassifTask(data = test_processed, target = "subscribe")

#normalize the variables
trainTask <- normalizeFeatures(trainTask,method = "standardize")
testTask <- normalizeFeatures(testTask,method = "standardize")

#Feature importance
im_feat <- generateFilterValuesData(trainTask, method = c("information.gain","chi.squared"))

Warning message:
"'Filter 'information.gain'' is deprecated.
Use 'Filter 'FSelector_information.gain' (package FSelector)' instead.
See help("Deprecated")"Warning message:
"'Filter 'chi.squared'' is deprecated.
Use 'Filter 'FSelector_chi.squared' (package FSelector)' instead.
See help("Deprecated")"

In [309]:
getParamSet("classif.rpart")

                   Type len  Def   Constr Req Tunable Trafo
minsplit        integer   -   20 1 to Inf   -    TRUE     -
minbucket       integer   -    - 1 to Inf   -    TRUE     -
cp              numeric   - 0.01   0 to 1   -    TRUE     -
maxcompete      integer   -    4 0 to Inf   -    TRUE     -
maxsurrogate    integer   -    5 0 to Inf   -    TRUE     -
usesurrogate   discrete   -    2    0,1,2   -    TRUE     -
surrogatestyle discrete   -    0      0,1   -    TRUE     -
maxdepth        integer   -   30  1 to 30   -    TRUE     -
xval            integer   -   10 0 to Inf   -   FALSE     -
parms           untyped   -    -        -   -    TRUE     -

In [310]:
#make tree learner
makeatree <- makeLearner("classif.rpart", predict.type = "prob")

#set 3 fold cross validation
set_cv <- makeResampleDesc("CV",iters = 3L)

In [311]:
#Search for hyperparameters
gs <- makeParamSet(
makeIntegerParam("minsplit",lower = 10, upper = 50),
makeIntegerParam("minbucket", lower = 5, upper = 50),
makeNumericParam("cp", lower = 0.001, upper = 0.2)
)

In [312]:
#do a grid search
gscontrol <- makeTuneControlGrid()

#hypertune the parameters
stune <- tuneParams(learner = makeatree, resampling = set_cv, task = trainTask, par.set = gs, control = ctrl)

[Tune] Started tuning learner classif.rpart for parameter set:
             Type len Def       Constr Req Tunable Trafo
minsplit  integer   -   -     10 to 50   -    TRUE     -
minbucket integer   -   -      5 to 50   -    TRUE     -
cp        numeric   -   - 0.001 to 0.2   -    TRUE     -
With control class: TuneControlGrid
Imputation value: 1
[Tune-x] 1: minsplit=10; minbucket=5; cp=0.001
[Tune-y] 1: mmce.test.mean=0.1171429; time: 0.0 min
[Tune-x] 2: minsplit=14; minbucket=5; cp=0.001
[Tune-y] 2: mmce.test.mean=0.1154762; time: 0.0 min
[Tune-x] 3: minsplit=19; minbucket=5; cp=0.001
[Tune-y] 3: mmce.test.mean=0.1140476; time: 0.0 min
[Tune-x] 4: minsplit=23; minbucket=5; cp=0.001
[Tune-y] 4: mmce.test.mean=0.1121429; time: 0.0 min
[Tune-x] 5: minsplit=28; minbucket=5; cp=0.001
[Tune-y] 5: mmce.test.mean=0.1128571; time: 0.0 min
[Tune-x] 6: minsplit=32; minbucket=5; cp=0.001
[Tune-y] 6: mmce.test.mean=0.1135714; time: 0.0 min
[Tune-x] 7: minsplit=37; minbucket=5; cp=0.001
[Tune-y] 7: 

In [313]:
#check best parameter
stune$x

#cross validation result
print(stune$y)

$minsplit
[1] 32

$minbucket
[1] 15

$cp
[1] 0.02311111

mmce.test.mean 
     0.1040476 


In [314]:
#using hyperparameters for modeling
t.tree <- setHyperPars(makeatree, par.vals = stune$x)

In [315]:
#train the model
t.rpart <- mlr::train(t.tree, trainTask)
getLearnerModel(t.rpart)

n= 4200 

node), split, n, loss, yval, (yprob)
      * denotes terminal node

1) root 4200 479 0 (0.88595238 0.11404762)  
  2) nr_employed>=-1.070057 3659 251 0 (0.93140202 0.06859798) *
  3) nr_employed< -1.070057 541 228 0 (0.57855823 0.42144177)  
    6) pdays>=-5.200201 423 145 0 (0.65721040 0.34278960) *
    7) pdays< -5.200201 118  35 1 (0.29661017 0.70338983) *

In [316]:
#make predictions
tpmodel <- predict(t.rpart, testTask)
performance(tpmodel, measures=mlr::auc)

auc 
0.7083732

In [317]:
#create a submission file
submit <- data.frame(client_id = test$client_id, subscribe = tpmodel$data$response)
write.csv(output, './data/Kaggle/output/rf_submission_7.csv', row.names=FALSE)

Decision Tree is doing no better than logistic regression. This algorithm has returned the auc of 0.708%.
So, one tree isn’t enough. Let’s build a SVM now.

### 3.4 SVM

In [361]:
#install.packages("kernlab")
library(kernlab)

In [362]:
#load svm
getParamSet("classif.ksvm")
ksvm <- makeLearner("classif.ksvm", predict.type = "prob")

                       Type  len    Def
scaled              logical    -   TRUE
type               discrete    -  C-svc
kernel             discrete    - rbfdot
C                   numeric    -      1
nu                  numeric    -    0.2
epsilon             numeric    -    0.1
sigma               numeric    -      -
degree              integer    -      3
scale               numeric    -      1
offset              numeric    -      1
order               integer    -      1
tol                 numeric    -  0.001
shrinking           logical    -   TRUE
class.weights numericvector <NA>      -
fit                 logical    -   TRUE
cache               integer    -     40
                                                Constr Req Tunable Trafo
scaled                                               -   -    TRUE     -
type              C-svc,nu-svc,C-bsvc,spoc-svc,kbb-svc   -    TRUE     -
kernel        vanilladot,polydot,rbfdot,tanhdot,lap...   -    TRUE     -
C                           

In [363]:
#Set parameters
pssvm <- makeParamSet(
makeDiscreteParam("C", values = 2^c(-8,-4,-2,0)), #cost parameters
makeDiscreteParam("sigma", values = 2^c(-8,-4,0,4)) #RBF Kernel Parameter
)

In [364]:
#specify search function
ctrl <- makeTuneControlGrid()

In [365]:
#tune model
res <- tuneParams(ksvm, task = trainTask, resampling = set_cv, par.set = pssvm, control = ctrl,measures = acc)

[Tune] Started tuning learner classif.ksvm for parameter set:
          Type len Def                   Constr Req Tunable Trafo
C     discrete   -   - 0.00390625,0.0625,0.25,1   -    TRUE     -
sigma discrete   -   -   0.00390625,0.0625,1,16   -    TRUE     -
With control class: TuneControlGrid
Imputation value: -0
[Tune-x] 1: C=0.00390625; sigma=0.00390625
[Tune-y] 1: acc.test.mean=0.8950000; time: 0.0 min
[Tune-x] 2: C=0.0625; sigma=0.00390625
[Tune-y] 2: acc.test.mean=0.8954762; time: 0.1 min
[Tune-x] 3: C=0.25; sigma=0.00390625
[Tune-y] 3: acc.test.mean=0.8954762; time: 0.1 min
[Tune-x] 4: C=1; sigma=0.00390625
[Tune-y] 4: acc.test.mean=0.8964286; time: 0.1 min
[Tune-x] 5: C=0.00390625; sigma=0.0625
[Tune-y] 5: acc.test.mean=0.8935714; time: 0.0 min
[Tune-x] 6: C=0.0625; sigma=0.0625
[Tune-y] 6: acc.test.mean=0.8914286; time: 0.0 min
[Tune-x] 7: C=0.25; sigma=0.0625
[Tune-y] 7: acc.test.mean=0.8890476; time: 0.1 min
[Tune-x] 8: C=1; sigma=0.0625
[Tune-y] 8: acc.test.mean=0.8950000;

In [366]:
#CV accuracy
res$y

acc.test.mean 
    0.8964286

In [367]:
#set the model with best params
t.svm <- setHyperPars(ksvm, par.vals = res$x)

In [368]:
#train
par.svm <- mlr::train(ksvm, trainTask)

In [369]:
#test
predict.svm <- predict(par.svm, testTask)
performance(predict.svm, measures=mlr::auc)

auc 
0.650983

In [327]:
#create a submission file
submit <- data.frame(client_id = test$client_id, subscribe = predict.svm$data$response)
write.csv(output, './data/Kaggle/output/rf_submission_8.csv', row.names=FALSE)

This model returns an auc of 0.0.684%.
Let’s do boosting now

### Gradient Boosting Machine

In [328]:
#load GBM
getParamSet("classif.gbm")
g.gbm <- makeLearner("classif.gbm", predict.type = "prob")

#specify tuning method
rancontrol <- makeTuneControlRandom(maxit = 50L)

#3 fold cross validation
set_cv <- makeResampleDesc("CV",iters = 3L)

                      Type len       Def
distribution      discrete   - bernoulli
n.trees            integer   -       100
cv.folds           integer   -         0
interaction.depth  integer   -         1
n.minobsinnode     integer   -        10
shrinkage          numeric   -       0.1
bag.fraction       numeric   -       0.5
train.fraction     numeric   -         1
keep.data          logical   -      TRUE
verbose            logical   -     FALSE
n.cores            integer   -         1
                                                    Constr Req Tunable Trafo
distribution      gaussian,bernoulli,huberized,adaboost...   -    TRUE     -
n.trees                                           1 to Inf   -    TRUE     -
cv.folds                                       -Inf to Inf   -    TRUE     -
interaction.depth                                 1 to Inf   -    TRUE     -
n.minobsinnode                                    1 to Inf   -    TRUE     -
shrinkage                                     

In [329]:
#parameters
gbm_par<- makeParamSet(
makeDiscreteParam("distribution", values = "bernoulli"),
makeIntegerParam("n.trees", lower = 100, upper = 1000), #number of trees
makeIntegerParam("interaction.depth", lower = 2, upper = 10), #depth of tree
makeIntegerParam("n.minobsinnode", lower = 10, upper = 80),
makeNumericParam("shrinkage",lower = 0.01, upper = 1)
)

# n.minobsinnode refers to the minimum number of observations in a tree node.
# shrinkage is the regulation parameter which dictates how fast / slow the algorithm should move.

In [330]:
#tune parameters
tune_gbm <- tuneParams(learner = g.gbm, task = trainTask,resampling = set_cv,measures = acc,
                       par.set = gbm_par,control = rancontrol)

[Tune] Started tuning learner classif.gbm for parameter set:
                      Type len Def       Constr Req Tunable Trafo
distribution      discrete   -   -    bernoulli   -    TRUE     -
n.trees            integer   -   - 100 to 1e+03   -    TRUE     -
interaction.depth  integer   -   -      2 to 10   -    TRUE     -
n.minobsinnode     integer   -   -     10 to 80   -    TRUE     -
shrinkage          numeric   -   -    0.01 to 1   -    TRUE     -
With control class: TuneControlRandom
Imputation value: -0
[Tune-x] 1: distribution=bernoulli; n.trees=649; interaction.depth=3; n.minobsinnode=61; shrinkage=0.698
[Tune-y] 1: acc.test.mean=0.8697619; time: 0.2 min
[Tune-x] 2: distribution=bernoulli; n.trees=913; interaction.depth=8; n.minobsinnode=16; shrinkage=0.118
[Tune-y] 2: acc.test.mean=0.8730952; time: 0.5 min
[Tune-x] 3: distribution=bernoulli; n.trees=814; interaction.depth=3; n.minobsinnode=29; shrinkage=0.802
[Tune-y] 3: acc.test.mean=0.8654762; time: 0.2 min
[Tune-x] 4: dist

In [331]:
#check CV accuracy
tune_gbm$y

acc.test.mean 
    0.8928571

In [332]:
#set parameters
final_gbm <- setHyperPars(learner = g.gbm, par.vals = tune_gbm$x)

In [333]:
#train
to.gbm <- mlr::train(final_gbm, trainTask)

In [334]:
#test
pr.gbm <- predict(to.gbm, testTask)
performance(pr.gbm, measures=mlr::auc)

auc 
0.7769769

In [335]:
#create a submission file
submit <- data.frame(client_id = test$client_id, subscribe = pr.gbm$data$response)
write.csv(output, './data/Kaggle/output/rf_submission_10.csv', row.names=FALSE)

The auc of this model is 0.777%. GBM performed better than SVM and Decision Tree, but couldn’t exceed random forest’s or Logistic Regression auc. Finally, let’s test XGboost also.

### XGboost

In [336]:
#load xgboost
set.seed(1001)
getParamSet("classif.xgboost")

#make learner with inital parameters
xg_set <- makeLearner("classif.xgboost", predict.type = "prob")
xg_set$par.vals <- list(
objective = "binary:logistic",
eval_metric = "error",
nrounds = 250
)

                                Type  len             Def
booster                     discrete    -          gbtree
watchlist                    untyped    -          <NULL>
eta                          numeric    -             0.3
gamma                        numeric    -               0
max_depth                    integer    -               6
min_child_weight             numeric    -               1
subsample                    numeric    -               1
colsample_bytree             numeric    -               1
colsample_bylevel            numeric    -               1
num_parallel_tree            integer    -               1
lambda                       numeric    -               1
lambda_bias                  numeric    -               0
alpha                        numeric    -               0
objective                    untyped    - binary:logistic
eval_metric                  untyped    -           error
base_score                   numeric    -             0.5
max_delta_step

In [337]:
#define parameters for tuning
xg_ps <- makeParamSet(
makeIntegerParam("nrounds",lower=200,upper=600),
makeIntegerParam("max_depth",lower=3,upper=20),
makeNumericParam("lambda",lower=0.55,upper=0.60),
makeNumericParam("eta", lower = 0.001, upper = 0.5),
makeNumericParam("subsample", lower = 0.10, upper = 0.80),
makeNumericParam("min_child_weight",lower=1,upper=5),
makeNumericParam("colsample_bytree",lower = 0.2,upper = 0.8)
)

In [338]:
#define search function
rancontrol <- makeTuneControlRandom(maxit = 100L) #do 100 iterations

#3 fold cross validation
set_cv <- makeResampleDesc("CV",iters = 3L)

#tune parameters
xg_tune <- tuneParams(learner = xg_set, task = trainTask, resampling = set_cv,measures = acc,par.set = xg_ps, control = rancontrol)

[Tune] Started tuning learner classif.xgboost for parameter set:
                    Type len Def       Constr Req Tunable Trafo
nrounds          integer   -   -   200 to 600   -    TRUE     -
max_depth        integer   -   -      3 to 20   -    TRUE     -
lambda           numeric   -   -  0.55 to 0.6   -    TRUE     -
eta              numeric   -   - 0.001 to 0.5   -    TRUE     -
subsample        numeric   -   -   0.1 to 0.8   -    TRUE     -
min_child_weight numeric   -   -       1 to 5   -    TRUE     -
colsample_bytree numeric   -   -   0.2 to 0.8   -    TRUE     -
With control class: TuneControlRandom
Imputation value: -0
[Tune-x] 1: nrounds=346; max_depth=19; lambda=0.557; eta=0.292; subsample=0.53; min_child_weight=2.63; colsample_bytree=0.381


[1]	train-error:0.107857 
[2]	train-error:0.106786 
[3]	train-error:0.097143 
[4]	train-error:0.097857 
[5]	train-error:0.096071 
[6]	train-error:0.093929 
[7]	train-error:0.095714 
[8]	train-error:0.092143 
[9]	train-error:0.093214 
[10]	train-error:0.092857 
[11]	train-error:0.092500 
[12]	train-error:0.090000 
[13]	train-error:0.092500 
[14]	train-error:0.090714 
[15]	train-error:0.091429 
[16]	train-error:0.091786 
[17]	train-error:0.088571 
[18]	train-error:0.089286 
[19]	train-error:0.088929 
[20]	train-error:0.087857 
[21]	train-error:0.086429 
[22]	train-error:0.086071 
[23]	train-error:0.087500 
[24]	train-error:0.088214 
[25]	train-error:0.085357 
[26]	train-error:0.086429 
[27]	train-error:0.085357 
[28]	train-error:0.085714 
[29]	train-error:0.083929 
[30]	train-error:0.083929 
[31]	train-error:0.083214 
[32]	train-error:0.082143 
[33]	train-error:0.083929 
[34]	train-error:0.083929 
[35]	train-error:0.083929 
[36]	train-error:0.084286 
[37]	train-error:0.082500 
[38]	train

[Tune-y] 1: acc.test.mean=0.8761905; time: 0.1 min
[Tune-x] 2: nrounds=442; max_depth=12; lambda=0.567; eta=0.273; subsample=0.369; min_child_weight=3.05; colsample_bytree=0.493


[1]	train-error:0.105357 
[2]	train-error:0.103929 
[3]	train-error:0.104286 
[4]	train-error:0.101071 
[5]	train-error:0.102500 
[6]	train-error:0.101429 
[7]	train-error:0.100357 
[8]	train-error:0.099643 
[9]	train-error:0.100000 
[10]	train-error:0.099286 
[11]	train-error:0.101429 
[12]	train-error:0.100714 
[13]	train-error:0.099643 
[14]	train-error:0.098571 
[15]	train-error:0.099643 
[16]	train-error:0.100000 
[17]	train-error:0.098571 
[18]	train-error:0.099643 
[19]	train-error:0.098571 
[20]	train-error:0.097500 
[21]	train-error:0.097500 
[22]	train-error:0.096786 
[23]	train-error:0.096071 
[24]	train-error:0.093929 
[25]	train-error:0.092500 
[26]	train-error:0.092500 
[27]	train-error:0.092857 
[28]	train-error:0.090000 
[29]	train-error:0.090714 
[30]	train-error:0.091071 
[31]	train-error:0.091071 
[32]	train-error:0.094286 
[33]	train-error:0.092857 
[34]	train-error:0.092143 
[35]	train-error:0.093214 
[36]	train-error:0.092857 
[37]	train-error:0.093929 
[38]	train

[Tune-y] 2: acc.test.mean=0.8771429; time: 0.1 min
[Tune-x] 3: nrounds=513; max_depth=20; lambda=0.571; eta=0.416; subsample=0.481; min_child_weight=1.89; colsample_bytree=0.347


...

[Tune-y] 98: acc.test.mean=0.8726190; time: 0.1 min
[Tune-x] 99: nrounds=485; max_depth=11; lambda=0.596; eta=0.325; subsample=0.485; min_child_weight=1.4; colsample_bytree=0.339


[1]	train-error:0.107857 
[2]	train-error:0.101071 
[3]	train-error:0.094286 
[4]	train-error:0.093929 
[5]	train-error:0.096071 
[6]	train-error:0.095714 
[7]	train-error:0.090000 
[8]	train-error:0.089286 
[9]	train-error:0.089286 
[10]	train-error:0.089286 
[11]	train-error:0.085714 
[12]	train-error:0.083571 
[13]	train-error:0.083929 
[14]	train-error:0.082857 
[15]	train-error:0.083929 
[16]	train-error:0.081786 
[17]	train-error:0.081786 
[18]	train-error:0.078929 
[19]	train-error:0.080357 
[20]	train-error:0.077500 
[21]	train-error:0.077857 
[22]	train-error:0.078571 
[23]	train-error:0.077500 
[24]	train-error:0.078929 
[25]	train-error:0.077857 
[26]	train-error:0.077857 
[27]	train-error:0.079286 
[28]	train-error:0.076786 
[29]	train-error:0.078929 
[30]	train-error:0.078571 
[31]	train-error:0.076786 
[32]	train-error:0.076071 
[33]	train-error:0.075714 
[34]	train-error:0.076786 
[35]	train-error:0.075357 
[36]	train-error:0.073214 
[37]	train-error:0.072500 
[38]	train

[Tune-y] 99: acc.test.mean=0.8700000; time: 0.2 min
[Tune-x] 100: nrounds=319; max_depth=9; lambda=0.553; eta=0.346; subsample=0.507; min_child_weight=4.25; colsample_bytree=0.203


[1]	train-error:0.113214 
[2]	train-error:0.115714 
[3]	train-error:0.105000 
[4]	train-error:0.103214 
[5]	train-error:0.103571 
[6]	train-error:0.102143 
[7]	train-error:0.101786 
[8]	train-error:0.102143 
[9]	train-error:0.102500 
[10]	train-error:0.102143 
[11]	train-error:0.098929 
[12]	train-error:0.099643 
[13]	train-error:0.099643 
[14]	train-error:0.100000 
[15]	train-error:0.100357 
[16]	train-error:0.098571 
[17]	train-error:0.098214 
[18]	train-error:0.099643 
[19]	train-error:0.099643 
[20]	train-error:0.098214 
[21]	train-error:0.099286 
[22]	train-error:0.099643 
[23]	train-error:0.099286 
[24]	train-error:0.098929 
[25]	train-error:0.096786 
[26]	train-error:0.097143 
[27]	train-error:0.097857 
[28]	train-error:0.097500 
[29]	train-error:0.096429 
[30]	train-error:0.097143 
[31]	train-error:0.095357 
[32]	train-error:0.094643 
[33]	train-error:0.096071 
[34]	train-error:0.094643 
[35]	train-error:0.093929 
[36]	train-error:0.093571 
[37]	train-error:0.092500 
[38]	train

[Tune-y] 100: acc.test.mean=0.8838095; time: 0.1 min
[Tune] Result: nrounds=391; max_depth=6; lambda=0.596; eta=0.00902; subsample=0.666; min_child_weight=3.35; colsample_bytree=0.27 : acc.test.mean=0.8985714


In [339]:
#set parameters
xg_new <- setHyperPars(learner = xg_set, par.vals = xg_tune$x)

In [340]:
#train model
xgmodel <- mlr::train(xg_new, trainTask)

[1]	train-error:0.112619 
[2]	train-error:0.112857 
[3]	train-error:0.111905 
[4]	train-error:0.111905 
[5]	train-error:0.107857 
[6]	train-error:0.103095 
[7]	train-error:0.102619 
[8]	train-error:0.100238 
[9]	train-error:0.101905 
[10]	train-error:0.101190 
[11]	train-error:0.100714 
[12]	train-error:0.102619 
[13]	train-error:0.102619 
[14]	train-error:0.102143 
[15]	train-error:0.100952 
[16]	train-error:0.099524 
[17]	train-error:0.100000 
[18]	train-error:0.099762 
[19]	train-error:0.100714 
[20]	train-error:0.100238 
[21]	train-error:0.100714 
[22]	train-error:0.100714 
[23]	train-error:0.100238 
[24]	train-error:0.100476 
[25]	train-error:0.100476 
[26]	train-error:0.100476 
[27]	train-error:0.100952 
[28]	train-error:0.100476 
[29]	train-error:0.100238 
[30]	train-error:0.099762 
[31]	train-error:0.099762 
[32]	train-error:0.100238 
[33]	train-error:0.100714 
[34]	train-error:0.100952 
[35]	train-error:0.100476 
[36]	train-error:0.100714 
[37]	train-error:0.100714 
[38]	train

In [341]:
#test model
predict.xg <- predict(xgmodel, testTask)
performance(predict.xg, measures=mlr::auc)

auc 
0.7957938

In [342]:
#create a submission file
submit <- data.frame(client_id = test$client_id, subscribe = predict.xg$data$response)
write.csv(output, './data/Kaggle/output/rf_submission_11.csv', row.names=FALSE)